In [ ]:
from tqdm import tqdm
from time import sleep
import pandas as pd
import json
import plotly.express as px
import plotly.graph_objects as go
from folium.plugins import MarkerCluster
import folium
import geopandas as gpd
from shapely.geometry import Point

In [ ]:
deals_df = pd.read_excel('Processed_Deals_df.xlsx', dtype={'Id': str, 'Contact Name': str})

# Географический анализ:


## 1. Проанализируйте географическое распределение сделок по городам.

* Загружаем JSON-справочник городов.
* Создаем функцию для извлечения координат и локализованных названий.
* Заполняем пропуски в колонке City значением "Unknown".
* Добавляем в DataFrame колонки с данными из справочника.

In [ ]:
cities = deals_df["City"].dropna().unique()
len(cities)

868

In [ ]:
with open("city.json", "r") as json_file:
    city_data = json.load(json_file)

def get_city_info(city):
    info = city_data.get(city, {})
    return pd.Series({
        'longitude': info.get('longitude', None),
        'latitude': info.get('latitude', None),
        'country_ru': info.get('country', None),
        'city_ru': info.get('formatted_address', None)
    })

deals_df['City'] = deals_df['City'].fillna('Unknown')

deals_df[['longitude', 'latitude', 'country_ru', 'city_ru']] = (
    deals_df['City'].apply(get_city_info)
)

In [ ]:
deals_df.loc[deals_df.City != "Unknown"].head(3)

Id Deal Owner Name Closing Date  Quality  \
32  5805028000056714532   Ulysses Adams          NaT      NaN   
39  5805028000056731279   Ulysses Adams          NaT      NaN   
49  5805028000056683030   Charlie Davis          NaT  C - Low   

                    Stage Lost Reason       Page               Campaign  \
32  Registered on Webinar         NaN   /webinar            webinar1906   
39  Registered on Webinar         NaN   /webinar                    NaN   
49    Waiting For Payment         NaN  /eng/test  performancemax_eng_DE   

            Content        Term  ... Initial Amount Paid (€)  \
32              NaN  invitation  ...                       0   
39              NaN         NaN  ...                       0   
49  _{region_name}_         NaN  ...                    1000   

   Offer Total Amount (€)         Contact Name        City Level of Deutsch  \
32                      0  5805028000044019127      Berlin          Unknown   
39                      0  5805028000054755989   Lahnstein          Unknown   
49                   9000  5805028000056690015  Crailsheim          Unknown   

    SLA Seconds  longitude   latitude  country_ru      city_ru  
32          NaN  13.404954  52.520007    Германия       Берлин  
39          NaN   7.609363  50.307827    Германия     Ланштайн  
49       1239.0  10.063357  49.133735    Германия  Крайльсхайм  

[3 rows x 27 columns]

In [ ]:
missing_cities = deals_df[deals_df['longitude'].isna()]['City'].unique()
print("Города, которых нет в JSON:", missing_cities)

Города, которых нет в JSON: ['Unknown' 'Helmstidde']


In [ ]:
geo_deals_df = deals_df[['Id', 'City']]
geo_deals_df_clean = geo_deals_df.dropna(subset=['City'])
deals_by_city = (
    geo_deals_df_clean
    .groupby('City')
    .size()
    .reset_index(name='Number of Deals')
)

deals_by_city_sorted = deals_by_city.sort_values(
    by='Number of Deals',
    ascending=False
)
deals_by_city_sorted.head()

City  Number of Deals
774   Unknown            16982
88     Berlin              263
521   München               87
288   Hamburg               78
570  Nürnberg               52

In [ ]:
geo_data_deals = (
    deals_df[["City", "longitude", "latitude", "country_ru", "city_ru"]]
    .drop_duplicates(subset=["City"])
    .dropna()
)
geo_data_deals.head()

City  longitude   latitude country_ru      city_ru
32      Berlin  13.404954  52.520007   Германия       Берлин
39   Lahnstein   7.609363  50.307827   Германия     Ланштайн
49  Crailsheim  10.063357  49.133735   Германия  Крайльсхайм
50    Prenzlau  13.862376  53.316844   Германия     Пренцлау
53    Dortmund   7.465298  51.513587   Германия     Дортмунд

In [ ]:
deals_by_city_sorted = deals_by_city_sorted[deals_by_city_sorted['City'] != "Unknown"]

fig = go.Figure(data=[
    go.Bar(
        name='Количество сделок',
        x=deals_by_city_sorted['City'].head(10),
        y=deals_by_city_sorted['Number of Deals'].head(10),
        marker=dict(color='#cfb09b')
    )
])

fig.update_layout(
    title="Топ 10 городов по количеству сделок",
    title_x=0.5,
    title_font=dict(size=24, color='black'),
    xaxis_tickangle=-45,
    showlegend=False,
    xaxis=dict(showgrid=False),
    yaxis=dict(showgrid=False, showticklabels=False),
    plot_bgcolor='white'
)

for i, value in enumerate(deals_by_city_sorted['Number of Deals'].head(10)):
    fig.add_annotation(
        x=deals_by_city_sorted['City'].head(10).iloc[i],
        y=value,
        text=str(value),
        showarrow=False,
        font=dict(size=14),
        align='center',
        yshift=10
    )

fig.show()

In [ ]:
geo_data = deals_df.groupby(['City', 'latitude', 'longitude'], as_index=False)['Id'].count()
geo_data.rename(columns={'Id': 'Number of Deals'}, inplace=True)

fig = px.scatter_geo(geo_data,
                     lat='latitude',
                     lon='longitude',
                     size='Number of Deals',
                     hover_name='City',
                     projection='natural earth',
                     title='Географическое распределение сделок')

fig.update_geos(
    showcoastlines=True,
    showland=True,
    showcountries=True,
    landcolor="lightgray",
    countrycolor="black"
)
fig.update_layout(title_x=0.5)
fig.show()

In [ ]:
geo_data = deals_df[deals_df['City'] != 'Unnamed'].dropna(subset="city_ru")

geometry = [Point(xy) for xy in zip(geo_data["longitude"], geo_data["latitude"])]

gdf = gpd.GeoDataFrame(geo_data, geometry=geometry)
gdf.set_crs(epsg=4326, inplace=True)

center = gdf.geometry.union_all().centroid
m = folium.Map(location=[center.y, center.x], zoom_start=4)

for idx, row in gdf.iterrows():
    folium.CircleMarker(
        location=[row.geometry.y, row.geometry.x],
        radius=3,
        color="red",
        fill=True,
        fill_color="red",
        popup=f"Index: {idx}"
    ).add_to(m)

m.save("deals_map.html")
m

In [ ]:
m = folium.Map(location=[center.y, center.x], zoom_start=4)
marker_cluster = MarkerCluster().add_to(m)

for _, row in gdf.iterrows():
    folium.Marker(
        location=[row.geometry.y, row.geometry.x],
        popup=f"Index: {idx}"
    ).add_to(marker_cluster)

m.save("deals_map_cluster.html")
m

***Географический анализ***

Основной кластер клиентов сосредоточен в Европе, особенно в Германии. Города, такие как Берлин, Лейпциг, Мюнхен, Гамбург и другие имеют наибольшее количество клиентов.  Это может быть связано с языковыми курсами, ориентированными на немецкий язык, либо с географической близостью школы к этому региону.

На карте также видны клиенты в других регионах:
В Северной Америке .
В Азии (несколько клиентов).
В Австралии (единичные клиенты).
В Южной Америке (единичные клиенты).
Наибольшая концентрация клиентов — в Европе, что подтверждается плотным скоплением точек в этом регионе.
Присутствие клиентов в других частях мира (США, Африка, Азия, Австралия) говорит о международном охвате, но эти регионы представлены значительно меньше.

***Анализ по языкам***

Большинство учеников находятся на уровнях B1 и B2, что соответствует среднему и выше среднего уровню владения языком . Это говорит о том, что школа, скорее всего, ориентирована на учеников, которые уже имеют базовые знания и стремятся улучшить свои навыки.
Уровни A1 и A2  представлены меньше, что может указывать на меньший спрос на курсы для новичков.
Уровень C1 также представлен слабо, а C2 почти отсутствует, что может означать, что школа не специализируется на продвинутом обучении.

***Рекомендации***

Учитывая концентрацию клиентов в Германии, школе стоит продолжать активно работать в этом регионе. Например, можно усилить маркетинг в крупных городах, таких как Берлин и Мюнхен, где уже есть значительное количество учеников.
Проведение оффлайн-мероприятий в этих городах может привлечь больше местных клиентов.
Для увеличения числа клиентов из  Азии и Америки можно разработать онлайн-курсы с гибким графиком, которые будут учитывать разницу во времени.
Партнёрства с образовательными учреждениями в этих регионах могут помочь привлечь больше студентов.
Для регионов вне Европы стоит адаптировать маркетинговые материалы под местные языки и культурные особенности. Например, в Африке можно использовать французский или арабский язык для рекламы, если школа ориентирована на эти
регионы.

Учитывая низкий спрос на начальные уровни языка, школа может разработать более привлекательные программы для новичков, например, интенсивные курсы или курсы с акцентом на разговорную практику.
Введение пробных бесплатных занятий для новичков может помочь привлечь больше учеников на эти уровни.

Для привлечения учеников на высокие уровни можно разработать специализированные курсы, например, подготовку к экзаменам (Goethe-Zertifikat, TestDaF) или курсы делового немецкого.
Партнёрство с университетами или компаниями, где требуется высокий уровень языка, может увеличить спрос на такие программы.
Поскольку большинство учеников находятся на уровнях B1-B2, школа может предложить дополнительные материалы, такие как разговорные клубы, тематические мастер-классы (например, по культуре Германии) или подготовку к экзаменам на этих уровнях.
Индивидуальные занятия или небольшие группы для этих уровней могут повысить удовлетворённость учеников.

Сохранение файла с преобразованиями

In [ ]:
deals_df.to_excel('/content/Geo_deals_df.xlsx', index=False)